In [1]:
from py_tools import parse_dataset
from typing import List
import numpy as np

In [2]:
dataset = parse_dataset()

In [3]:
len(dataset.data)

40546

In [4]:
dataset.lasers[0][0].scan.shape[0]

180

In [5]:
a,b = dataset.lasers[0][0].XY
a.shape

(180,)

In [6]:
import matplotlib.pyplot as plt
from matplotlib import animation, rc
from IPython.display import display, Math, Latex, Markdown, HTML

# Some Visualization

## Laser Scans alone 

To test if we parsed the dataset correctly

In [7]:
def animate_lidar(lidar_scans: List['np.array'], xlim, ylim, frames, fps = 30):
    fig = plt.figure(figsize=(10, 6))
    anim_ax = fig.add_subplot(111)
    if xlim != None and ylim != None:
        anim_ax.set(xlim=xlim, ylim=ylim)
    anim_ax.set_aspect('equal')
    plt.close()
    x_laser, y_laser = lidar_scans[0]
    # Prepare Laser data.
    laser_line, = anim_ax.plot(x_laser, y_laser, 'o', color='orangered')

    def animate(i):
        start_frame = frames[1]
        skip_frames = frames[2]
        next_frame = start_frame + i*(skip_frames+1)
        laser = lidar_scans[next_frame]
        x_p, y_p = laser
        laser_line.set_data(x_p, y_p)
        return (laser_line,)
    
    anim = animation.FuncAnimation(fig, animate,
                                   frames=frames[1], # len(data.lasers)
                                   interval=500, 
                                   blit=True)
    return HTML(anim.to_jshtml(fps = fps))

In [8]:
lidar_scans = [scan[0].XY for scan in dataset.lasers]

In [9]:
animate_lidar(lidar_scans, xlim=(-20,20), ylim=(-1,25), frames=(150, 200, 5))

## Using the odometery alone to draw trajectory

In [10]:
def animate_path(path: 'np.array', xlim, ylim, frames, fps = 30):
    fig = plt.figure(figsize=(10, 6))
    anim_ax = fig.add_subplot(111)
    if xlim != None and ylim != None:
        anim_ax.set(xlim=xlim, ylim=ylim)
    anim_ax.set_aspect('equal')
    plt.close()
    x_p, y_p = [path[0,0]], [path[1,0]]
    # Prepare Laser data.
    laser_line, = anim_ax.plot(x_p, y_p, '-', color='blue')

    def animate(i):
        start_frame = frames[1]
        skip_frames = frames[2]
        end_frame = start_frame + i*(skip_frames+1)
        x_p, y_p = path[:, :end_frame]
        laser_line.set_data(x_p, y_p)
        return (laser_line,)
    
    anim = animation.FuncAnimation(fig, animate,
                                   frames=frames[1], # len(data.lasers)
                                   interval=500, 
                                   blit=True)
    return HTML(anim.to_jshtml(fps = fps))

In [11]:
path = np.array([np.array([scan[0].x, scan[0].y]).reshape(2,1) for scan in dataset.lasers]).squeeze().T
path.shape

(2, 13631)

In [12]:
animate_path(path, xlim=(-60,25), ylim=(-40,25), frames=(150, 200+30, int((len(dataset.lasers) - 150)/200 ) ))

## Map with only Odometry data

In [ ]:
def animate_map(map_data: List['np.array'], xlim, ylim, frames, fps = 30):
    fig = plt.figure(figsize=(10, 6))
    anim_ax = fig.add_subplot(111)
    if xlim != None and ylim != None:
        anim_ax.set(xlim=xlim, ylim=ylim)
    anim_ax.set_aspect('equal')
    plt.close()
    x_p, y_p = [path[0,0]], [path[1,0]]
    # Prepare Laser data.
    laser_line, = anim_ax.plot(x_p, y_p, '-', color='blue')

    def animate(i):
        start_frame = frames[1]
        skip_frames = frames[2]
        end_frame = start_frame + i*(skip_frames+1)
        x_p, y_p = path[:, :end_frame]
        laser_line.set_data(x_p, y_p)
        return (laser_line,)
    
    anim = animation.FuncAnimation(fig, animate,
                                   frames=frames[1], # len(data.lasers)
                                   interval=500, 
                                   blit=True)
    return HTML(anim.to_jshtml(fps = fps))

In [16]:
print(min([scan[0].theta for scan in dataset.lasers]), max([scan[0].theta for scan in dataset.lasers]))

-3.136677 3.140363


In [25]:
from math import sin, cos
def v2m(x,y,theta):
    rotation = np.array([[cos(theta), sin(theta)],[-sin(theta), cos(theta)]])
    translation = np.array([[x],[y]], dtype = np.float)
    transformation = np.identity(3, dtype=np.float)
    transformation[:2,:2] = rotation
    transformation[:2,[2]] = translation
    return transformation

[[ 7.96326711e-04  9.99999683e-01  1.00000000e+00]
 [-9.99999683e-01  7.96326711e-04  2.00000000e+00]
 [ 0.00000000e+00  0.00000000e+00  1.00000000e+00]]


In [ ]:
point_cloud = []
for laser in dataset.lasers:
    transformation = v2m(laser.x, laser.y, laser.theta)
    